# Klasifikace vín
Cílem tohoto projektu je naučit klasifikátor ze souboru slovního popisu vín (aroma, kyselinka...) a odrůd. Používáme standardní balíčky pro strojové učení Scikit Learn (https://scikit-learn.org/stable/index.html), datovou analytiku Pandas (https://pandas.pydata.org/), vizualizaci dat Yellowbrick (https://www.scikit-yb.org/en/latest/). Je potřeba mít python3.

In [1]:
!pip install sklearn --user
!pip install pandas --user
!pip install yellowbrick --user

You are using pip version 19.0.3, however version 19.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
You are using pip version 19.0.3, however version 19.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
You are using pip version 19.0.3, however version 19.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


Balíček collections je standardem v pythonu, použijeme Counter na zjištění, které odrůdy jsou v datovém souboru nejčetnější. Kdyby nefungovalo `from sklearn.model_selection import train_test_split`, změňte jej na `from sklearn.cross_validation import train_test_split`, v různých verzích sklearn je to různě.

In [2]:
import numpy as np
from sklearn.naive_bayes import MultinomialNB
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
from collections import Counter
from sklearn.model_selection import train_test_split

Jako trénovací i testovací data použijeme datový soubor Wine Reviews (https://www.scikit-yb.org/en/latest/). V Jupyter Notebooku je snadné vypsat obsah proměnné tím, že ji napíšeme na poslední místo slotu (zde `df`). Balíček pandas v tomto případě zajistí, že se DataFrame vypíše jako naformátovaná tabulka. Srovnejte s tím, jak vypadá soubor wine_data.csv v textovém editoru, případně jej můžete zkusit otevřít v Excelu, Libre Office Calc apod. 

In [3]:
df = pd.read_csv('data/wine_data.csv')
df

Unnamed: 0      country  \
0                0        Italy   
1                1     Portugal   
2                2           US   
3                3           US   
4                4           US   
5                5        Spain   
6                6        Italy   
7                7       France   
8                8      Germany   
9                9       France   
10              10           US   
11              11       France   
12              12           US   
13              13        Italy   
14              14           US   
15              15      Germany   
16              16    Argentina   
17              17    Argentina   
18              18        Spain   
19              19           US   
20              20           US   
21              21           US   
22              22        Italy   
23              23           US   
24              24        Italy   
25              25           US   
26              26        Italy   
27              27        Italy   
28              28        Italy   
29              29           US   
...            ...          ...   
129941      129941           US   
129942      129942           US   
129943      129943        Italy   
129944      129944       Israel   
129945      129945           US   
129946      129946      Germany   
129947      129947        Italy   
129948      129948    Argentina   
129949      129949           US   
129950      129950           US   
129951      129951       France   
129952      129952           US   
129953      129953  New Zealand   
129954      129954  New Zealand   
129955      129955  New Zealand   
129956      129956  New Zealand   
129957      129957        Spain   
129958      129958  New Zealand   
129959      129959       France   
129960      129960     Portugal   
129961      129961        Italy   
129962      129962        Italy   
129963      129963       Israel   
129964      129964       France   
129965      129965       France   
129966      129966      Germany   
129967      129967           US   
129968      129968       France   
129969      129969       France   
129970      129970       France   

                                              description  \
0       Aromas include tropical fruit, broom, brimston...   
1       This is ripe and fruity, a wine that is smooth...   
2       Tart and snappy, the flavors of lime flesh and...   
3       Pineapple rind, lemon pith and orange blossom ...   
4       Much like the regular bottling from 2012, this...   
5       Blackberry and raspberry aromas show a typical...   
6       Here's a bright, informal red that opens with ...   
7       This dry and restrained wine offers spice in p...   
8       Savory dried thyme notes accent sunnier flavor...   
9       This has great depth of flavor with its fresh ...   
10      Soft, supple plum envelopes an oaky structure ...   
11      This is a dry wine, very spicy, with a tight, ...   
12      Slightly reduced, this wine offers a chalky, t...   
13      This is dominated by oak and oak-driven aromas...   
14      Building on 150 years and six generations of w...   
15      Zesty orange peels and apple notes abound in t...   
16      Baked plum, molasses, balsamic vinegar and che...   
17      Raw black-cherry aromas are direct and simple ...   
18      Desiccated blackberry, leather, charred wood a...   
19      Red fruit aromas pervade on the nose, with cig...   
20      Ripe aromas of dark berries mingle with ample ...   
21      A sleek mix of tart berry, stem and herb, alon...   
22      Delicate aromas recall white flower and citrus...   
23      This wine from the Geneseo district offers aro...   
24      Aromas of prune, blackcurrant, toast and oak c...   
25      Oak and earth intermingle around robust aromas...   
26      Pretty aromas of yellow flower and stone fruit...   
27      Aromas recall ripe dark berry, toast and a whi...   
28      Aromas suggest mature berry, scorched earth, a...   
29     

V DataFrame je možné ke sloupcům přistupovat jako ke slovníku (python `dict`), a tudíž je možné vybrat je sloupec se jménem odrůdy. Pro naše účely vybereme 10 nejčetnějších odrůd.

In [4]:
counter = Counter(df['variety'].tolist())
df = df[df['variety'].map(lambda x: x in [a for a,b in counter.most_common(10)])]
df

Unnamed: 0      country  \
3                3           US   
4                4           US   
10              10           US   
12              12           US   
14              14           US   
15              15      Germany   
20              20           US   
21              21           US   
23              23           US   
25              25           US   
28              28        Italy   
31              31        Italy   
33              33           US   
34              34           US   
35              35           US   
37              37        Italy   
41              41           US   
43              43           US   
44              44        Chile   
45              45           US   
47              47           US   
48              48           US   
50              50        Italy   
54              54        Italy   
55              55           US   
56              56           US   
58              58        Chile   
60              60           US   
64              64           US   
65              65       France   
...            ...          ...   
129913      129913           US   
129914      129914           US   
129915      129915           US   
129918      129918      Germany   
129919      129919           US   
129920      129920           US   
129922      129922      Austria   
129923      129923      Germany   
129924      129924      Germany   
129925      129925    Argentina   
129926      129926           US   
129928      129928        Spain   
129931      129931       France   
129932      129932    Argentina   
129935      129935           US   
129936      129936       France   
129940      129940           US   
129941      129941           US   
129942      129942           US   
129943      129943        Italy   
129946      129946      Germany   
129947      129947        Italy   
129949      129949           US   
129955      129955  New Zealand   
129956      129956  New Zealand   
129958      129958  New Zealand   
129960      129960     Portugal   
129963      129963       Israel   
129966      129966      Germany   
129967      129967           US   

                                              description  \
3       Pineapple rind, lemon pith and orange blossom ...   
4       Much like the regular bottling from 2012, this...   
10      Soft, supple plum envelopes an oaky structure ...   
12      Slightly reduced, this wine offers a chalky, t...   
14      Building on 150 years and six generations of w...   
15      Zesty orange peels and apple notes abound in t...   
20      Ripe aromas of dark berries mingle with ample ...   
21      A sleek mix of tart berry, stem and herb, alon...   
23      This wine from the Geneseo district offers aro...   
25      Oak and earth intermingle around robust aromas...   
28      Aromas suggest mature berry, scorched earth, a...   
31      Merlot and Nero d'Avola form the base for this...   
33      Rustic and dry, this has flavors of berries, c...   
34      This shows a tart, green gooseberry flavor tha...   
35      As with many of the Erath 2010 vineyard design...   
37      This concentrated Cabernet offers aromas of cu...   
41      A stiff, tannic wine, this slowly opens and br...   
43      The clean, brisk mouthfeel gives this slightly...   
44      A berry aroma comes with cola and herb notes. ...   
45      Right out of the starting blocks this is an oa...   
47      This is a sweet wine with flavors of white sug...   
48      This bottling resembles the New Zealand paradi...   
50      This blend of Nero d'Avola and Syrah opens wit...   
54      A blend of Nero d'Avola and Nerello Mascalese,...   
55      This shows jelly-like flavors of orange and pe...   
56      This is weighty, creamy and medium to full in ...   
58      Lightly herbal strawberry and raspberry aromas...   
60      Syrupy and dense, this wine is jammy in plum a...   
64      There are intriguing touches to the nose of th...   
65     

LabelEncoder se bude hodit pro vizualizaci dat. Každá odrůda (třída) dostane má svoje číslo, LabelEncoder překódovává toto číslo na jméno odrůdy a naopak.

In [5]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
le.fit(df['variety'])
print("classes", le.classes_)
print("classes indices", le.transform(le.classes_))
le.transform(['Cabernet Sauvignon', 'Pinot Noir', 'Riesling'])

classes ['Bordeaux-style Red Blend' 'Cabernet Sauvignon' 'Chardonnay' 'Merlot'
 'Pinot Noir' 'Red Blend' 'Riesling' 'Rosé' 'Sauvignon Blanc' 'Syrah']
classes indices [0 1 2 3 4 5 6 7 8 9]


array([1, 4, 6])

Jak zhruba vypadá popis vína (můžete změnit číslo, ale pozor, teď máme v DataFrame jen některé řádky (10 nejčastějších odrůd).

In [6]:
print("description of wine no. 3:",df.loc[3,]["description"])

description of wine no. 3: Pineapple rind, lemon pith and orange blossom start off the aromas. The palate is a bit more opulent, with notes of honey-drizzled guava and mango giving way to a slightly astringent, semidry finish.


Proměnná `varietal_list` bude obsahovat řadu čísel odrůd. Algoritmy strojového učení dostanou na vstup matici rysů (řádky jsou jednotlivé instance, v našem případě konkrétní láhve vína, sloupce jsou v našem případě popisy) a vektor tříd (v našem případě čísla odrůd). Matice se označuje X, vektor se označuje Y. Klasifikátor se potom učí:

    [X ... ]       [Y]
    |  .   |       |.|
    |   .  |   =   |.|
    |    . |       |.|
    [     X]       [.]

In [7]:
description_list = df['description'].tolist()
varietal_list = le.transform(df['variety'].tolist())
print(varietal_list)

[6 4 1 ... 1 6 4]


Nejdůležitější část se odehrává zde. Za prvé je třeba převést slovní popisy na vektory (to budou řádky matice X). Z řady možností, jak to udělat, jsem zvolila TF-IDF, což je technika, která počítá důležitost slova oproti korpusovým datům (viz https://cs.wikipedia.org/wiki/Tf-idf). Výsledný vektor bude pro každé slovo obsažené v popisu obsahovat jeho "klíčovost", tj. jak moc je charakteristické právě pro tento popis. 

Za druhé je třeba zvolit algoritmus strojového učení, v tomto případě naivní Bayesovský klasifikátor (NB) pro více tříd (Multinomial). 

DataFrame rozdělíme na trénovací a testovací sady v poměru 7:3 (parametr `test_size`).

Trénování probíhá voláním funkce `fit()`. Aplikace na testovací sadu probíhá pomocí metody `predict()`.

Ve for-cyklu se potom počítá, kolik predikcí bylo správných. Vypisují se ty špatné. Zkuste je zběžně prohlédnout a vyvodit nějaké závěry, např. které dvojice tříd klasifikátor častěji zaměňuje?

In [8]:
tfidf_vectorizer = TfidfVectorizer()
x_train_tfidf = tfidf_vectorizer.fit_transform(description_list)

train_x, test_x, train_y, test_y = train_test_split(x_train_tfidf, varietal_list, test_size=0.3)

model = MultinomialNB()
clf = model.fit(train_x, train_y)
y_pred = clf.predict(test_x)

n_right = 0
for i in range(len(y_pred)):
    if y_pred[i] == test_y[i]:
        n_right += 1
    else:
        print(y_pred[i], le.inverse_transform([y_pred[i]])[0], test_y[i], le.inverse_transform([test_y[i]])[0])

print("Accuracy: %.2f%%" % ((n_right/float(len(test_y)) * 100)))

4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 7 Rosé
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 9 Syrah
5 Red Blend 3 Merlot
2 Chardonnay 6 Riesling
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 9 Syrah
4 Pinot Noir 5 Red Blend
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 9 Syrah
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 4 Pinot Noir
5 Red Blend 9 Syrah
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 5 Red Blend
1 Cabernet Sauvignon 9 Syrah
4 Pinot Noir 7 Rosé
4 Pinot Noir 5 Red Blend
4 Pinot Noir 6 Riesling
4 Pinot Noir 3 Merlot
2 Chardonnay 6 Riesling
4 Pinot Noir 7 Rosé
4 Pinot Noir 2 Chardonnay
4 Pinot Noir 7 Rosé
0 Bordeaux-style Red Blend 4 Pinot Noir
2 Chardonnay 6 Riesling
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 9 Syrah
4 Pinot Noir 6 Riesling
4 Pinot Noir 6 Riesling
2 Chardonnay 6 Riesling
4 Pinot Noir 7 Rosé
4 Pinot Noir 3 Merlot
5 Red Blend 1 Cabernet Sa

2 Chardonnay 8 Sauvignon Blanc
0 Bordeaux-style Red Blend 3 Merlot
4 Pinot Noir 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 0 Bordeaux-style Red Blend
2 Chardonnay 7 Rosé
5 Red Blend 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
0 Bordeaux-style Red Blend 2 Chardonnay
5 Red Blend 0 Bordeaux-style Red Blend
4 Pinot Noir 5 Red Blend
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 7 Rosé
4 Pinot Noir 3 Merlot
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 7 Rosé
4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 7 Rosé
4 Pinot Noir 0 Bordeaux-style Red Blend
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 8 Sauvignon Blanc
4 Pinot Noir 5 Red Blend
4 Pinot Noir 0 Bordeaux-style Red Blend
2 Chardonnay 7 Rosé
1 Cabernet Sauvignon 5 Red Blend
4 Pinot Noir 9 Syrah
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 6 Riesling
5 Red Blend 9 Syrah

4 Pinot Noir 5 Red Blend
0 Bordeaux-style Red Blend 4 Pinot Noir
5 Red Blend 3 Merlot
4 Pinot Noir 3 Merlot
4 Pinot Noir 5 Red Blend
4 Pinot Noir 0 Bordeaux-style Red Blend
4 Pinot Noir 0 Bordeaux-style Red Blend
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 5 Red Blend
6 Riesling 8 Sauvignon Blanc
1 Cabernet Sauvignon 5 Red Blend
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 6 Riesling
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 0 Bordeaux-style Red Blend
0 Bordeaux-style Red Blend 3 Merlot
2 Chardonnay 4 Pinot Noir
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 6 Riesling
1 Cabernet Sauvignon 4 Pinot Noir
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 0 Bordeaux-style Red Blend
0 Bordeaux-style Red Blend 4 Pinot Noir
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir

5 Red Blend 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 3 Merlot
4 Pinot Noir 9 Syrah
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 3 Merlot
5 Red Blend 1 Cabernet Sauvignon
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 7 Rosé
4 Pinot Noir 9 Syrah
5 Red Blend 7 Rosé
1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 9 Syrah
5 Red Blend 0 Bordeaux-style Red Blend
2 Chardonnay 6 Riesling
4 Pinot Noir 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 7 Rosé
5 Red Blend 0 Bordeaux-style Red Blend
0 Bordeaux-style Red Blend 7 Rosé
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
0 Bordeaux-style Red Blend 4 Pinot Noir
1 Cabernet Sauvignon 5 Red Blend
2 Chardonnay 6 Riesling
4 Pinot Noir 2 Chardonnay
4 Pinot Noir 

4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 5 Red Blend
5 Red Blend 9 Syrah
4 Pinot Noir 9 Syrah
4 Pinot Noir 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 9 Syrah
4 Pinot Noir 2 Chardonnay
1 Cabernet Sauvignon 5 Red Blend
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 1 Cabernet Sauvignon
5 Red Blend 0 Bordeaux-style Red Blend
5 Red Blend 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
1 Cabernet Sauvignon 5 Red Blend
5 Red Blend 0 Bordeaux-style Red Blend
4 Pinot Noir 9 Syrah
5 Red Blend 7 Rosé
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 5 Red Blend
5 Red Blend 7 Rosé
4 Pinot Noir 5 Red Blend
0 Bordeaux-style Red Blend 4 Pinot Noir
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 0 Bordeaux-style Red Blend
4 Pinot Noir 1 Cabernet Sauvignon
0 Bordeaux-style Red Blend 4 Pinot Noir
5 Red Blend 3 Merlot
1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 1 Cabernet

...

2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 3 Merlot
5 Red Blend 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 0 Bordeaux-style Red Blend
1 Cabernet Sauvignon 9 Syrah
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 7 Rosé
5 Red Blend 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 9 Syrah
4 Pinot Noir 9 Syrah
0 Bordeaux-style Red Blend 4 Pinot Noir
4 Pinot Noir 5 Red Blend
4 Pinot Noir 9 Syrah
4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 7 Rosé
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 6 Riesling
5 Red Blend 1 Cabernet Sauvignon
4 Pinot Noir 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 7 Rosé
4 Pinot Noir 0 Bordeaux-style Red Blend
5 Red Blend 7 Rosé
4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 4 Pinot Noir
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 3 Merlot
1 Cabern

2 Chardonnay 6 Riesling
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 9 Syrah
5 Red Blend 0 Bordeaux-style Red Blend
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 5 Red Blend
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 6 Riesling
5 Red Blend 1 Cabernet Sauvignon
5 Red Blend 1 Cabernet Sauvignon
2 Chardonnay 7 Rosé
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 7 Rosé
4 Pinot Noir 9 Syrah
0 Bordeaux-style Red Blend 3 Merlot
4 Pinot Noir 7 Rosé
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 5 Red Blend
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 7 Rosé
2 Chardonnay 7 Rosé
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 9 Syrah
2 Chardonnay 6 Riesling
4 Pinot Noir 7 Rosé
2 Chardonnay 6 Riesling
4 Pinot Noir 9 Syrah
4 Pinot Noir 7 Rosé
4 Pinot Noir 3 Merlot
4 Pinot Noir 

2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 3 Merlot
4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 5 Red Blend
4 Pinot Noir 3 Merlot
4 Pinot Noir 5 Red Blend
2 Chardonnay 8 Sauvignon Blanc
1 Cabernet Sauvignon 5 Red Blend
2 Chardonnay 7 Rosé
4 Pinot Noir 0 Bordeaux-style Red Blend
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 8 Sauvignon Blanc
4 Pinot Noir 7 Rosé
4 Pinot Noir 0 Bordeaux-style Red Blend
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 1 Cabernet Sauvignon
1 Cabernet Sauvignon 4 Pinot Noir
1 Cabernet Sauvignon 4 Pinot Noir
4 Pinot Noir 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
5 Red Blend 0 Bordeaux-style Red Blend
4 Pinot Noir 7 Rosé
1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 9 Syrah
1 Cabernet Sauvignon 5 Red Blend
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 9 Syrah
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 5 Red Blend
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 9 Syrah
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon

1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 7 Rosé
0 Bordeaux-style Red Blend 7 Rosé
0 Bordeaux-style Red Blend 4 Pinot Noir
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 3 Merlot
1 Cabernet Sauvignon 5 Red Blend
4 Pinot Noir 9 Syrah
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 4 Pinot Noir
5 Red Blend 1 Cabernet Sauvignon
5 Red Blend 0 Bordeaux-style Red Blend
2 Chardonnay 6 Riesling
5 Red Blend 0 Bordeaux-style Red Blend
1 Cabernet Sauvignon 3 Merlot
2 Chardonnay 7 Rosé
4 Pinot Noir 2 Chardonnay
1 Cabernet Sauvignon 5 Red Blend
5 Red Blend 9 Syrah
4 Pinot Noir 1 Cabernet Sauvignon
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 2 Chardonnay
5 Red Blend 1 Cabernet Sauvignon
4 Pinot Noir 1 Cabernet Sauvignon
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 5 Red Blend
4 Pinot Noir 9 Syrah
2 Chardonnay 5 Red Blend
1 Cabernet Sauvignon

0 Bordeaux-style Red Blend 2 Chardonnay
1 Cabernet Sauvignon 5 Red Blend
2 Chardonnay 8 Sauvignon Blanc
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
5 Red Blend 1 Cabernet Sauvignon
4 Pinot Noir 7 Rosé
1 Cabernet Sauvignon 3 Merlot
4 Pinot Noir 9 Syrah
4 Pinot Noir 8 Sauvignon Blanc
2 Chardonnay 6 Riesling
1 Cabernet Sauvignon 3 Merlot
1 Cabernet Sauvignon 4 Pinot Noir
2 Chardonnay 8 Sauvignon Blanc
1 Cabernet Sauvignon 9 Syrah
2 Chardonnay 8 Sauvignon Blanc
5 Red Blend 3 Merlot
2 Chardonnay 6 Riesling
5 Red Blend 9 Syrah
4 Pinot Noir 7 Rosé
4 Pinot Noir 7 Rosé
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 5 Red Blend
1 Cabernet Sauvignon 0 Bordeaux-style Red Blend
4 Pinot Noir 3 Merlot
2 Chardonnay 6 Riesling
4 Pinot Noir 2 Chardonnay
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 1 Cabernet Sauvignon
2 Chardonnay 8 Sauvignon Blanc
4 Pinot Noir 9 Syrah
4 Pinot Noir 9 Syrah
4 Pinot Noir 9 Syrah
4 Pinot Noir 3 Merlot
2 Chardonnay 6 Riesling
5 Red Blend 0 Bordeaux-style Re

Z předchozího je vidět, že klasifikátor málokdy splete bílé a červené víno. Taky je vidět, že často zaměňuje chardonnay a sauvignon, cabernet sauvignon a pinot noir, případně další dvojice červených vín.

V následující vizualizaci je vidět kompletní matice záměn, která předchozí pozorování potvrzuje a zároveň ukazuje, proč je chardonnay a pinot noir nejčastěji v předchozím výpisu. Pokud nevidíte obrázek, spusťte následující část kódu podruhé.

In [9]:
from yellowbrick.classifier import ConfusionMatrix
cm = ConfusionMatrix(model, classes=le.classes_, label_encoder=le) 

# To create the ConfusionMatrix, we need some test data. Score runs predict() on the data
# and then creates the confusion_matrix from scikit-learn.
cm.score(test_x, test_y)

# How did we do?
cm.poof()
#cm.draw()

<Figure size 800x550 with 1 Axes>

Pro klasifikaci do více tříd je zajímavé uvádět přesnost, pokrytí a F-míry pro každou třídu zvlášť. Ukáže se, na které třídy nemá cenu klasifikátor používat, zde např. merlot nebo syrah.

In [10]:
from sklearn.metrics import classification_report
print(classification_report(test_y, y_pred, target_names=le.classes_))

                          precision    recall  f1-score   support

Bordeaux-style Red Blend       0.76      0.59      0.66      2127
      Cabernet Sauvignon       0.56      0.68      0.61      2777
              Chardonnay       0.62      0.96      0.76      3539
                  Merlot       0.00      0.00      0.00       963
              Pinot Noir       0.53      0.90      0.67      3954
               Red Blend       0.71      0.74      0.72      2679
                Riesling       0.95      0.52      0.67      1570
                    Rosé       0.97      0.15      0.25      1101
         Sauvignon Blanc       0.96      0.25      0.39      1498
                   Syrah       0.96      0.02      0.04      1189

               micro avg       0.63      0.63      0.63     21397
               macro avg       0.70      0.48      0.48     21397
            weighted avg       0.68      0.63      0.58     21397



/home/popelucha/.local/lib/python3.5/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
